## Testing variable-gateset-dimension GST with model selection

###     Setup

In [1]:
import pygsti
%pylab inline

Populating the interactive namespace from numpy and matplotlib


In [2]:
#Load gateset and some string lists
gs_target = pygsti.io.load_gateset("tutorial_files/Example_Gateset.txt")
fiducialList = pygsti.io.load_gatestring_list("tutorial_files/Example_FiducialList.txt")
germList = pygsti.io.load_gatestring_list("tutorial_files/Example_GermsList.txt")
specs = pygsti.construction.build_spam_specs(fiducialList)
expList = [1,2,4]


In [3]:
#Create some testing gate string lists
lgstList = pygsti.construction.list_lgst_gatestrings(specs, gs_target.keys())
lsgstLists = [ lgstList[:] ]
for exp in expList:
    gsList = pygsti.construction.create_gatestring_list(
                "f0+germ*exp+f1", f0=fiducialList, f1=fiducialList,
                germ=germList, exp=exp, order=['germ','f0','f1'])
    lsgstLists.append( lsgstLists[-1] +  gsList )
    
dsList = pygsti.remove_duplicates( lsgstLists[-1] )

In [5]:
#Test on fake data by depolarizing target set, increasing it's dimension,
# and adding leakage to the gates into the new dimension.

gs_dataGen4 = gs_target.depolarize(gate_noise=0.1)
gs_dataGen5 = gs_dataGen4.increase_dimension(5)
leakGate = pygsti.construction.build_gate( [2,1],[('Q0',),('L0',)] , "LX(pi/4.0,0,2)","gm") # X(pi,Q0)*LX(pi,0,2)

gs_dataGen5.set_gate('Gx', pygsti.objects.compose( gs_dataGen5.get_gate('Gx'), leakGate))
gs_dataGen5.set_gate('Gy', pygsti.objects.compose( gs_dataGen5.get_gate('Gy'), leakGate))
print gs_dataGen5.keys()

#Some debugging...
#NOTE: with LX(pi,0,2) above, dim 5 test will choose a dimension 3 gateset, which may be sensible
#       looking at the gate matrices in this case... but maybe LX(pi,...) is faulty?
#print gs_dataGen4
#print gs_dataGen5

#Jmx = GST.JOps.jamiolkowski_iso(gs_dataGen4['Gx'])
#Jmx = GST.JOps.jamiolkowski_iso(gs_dataGen5['Gx'],dimOrStateSpaceDims=[2,1])
#print "J = \n",Jmx
#print "evals = ",eigvals(Jmx)

dsFake4 = pygsti.construction.generate_fake_data(gs_dataGen4, dsList, nSamples=1000000, sampleError="binomial", seed=1234)
dsFake5 = pygsti.construction.generate_fake_data(gs_dataGen5, dsList, nSamples=1000000, sampleError="binomial", seed=1234)

['Gi', 'Gx', 'Gy']


In [6]:
print "Number of gates = ",len(gs_target.keys())
print "Number of fiducials =",len(fiducialList)
print "Maximum length for a gate string in ds =",max(map(len,dsList))
print "Number of LGST strings = ",len(lgstList)
print "Number of LSGST strings = ",map(len,lsgstLists)

Number of gates =  3
Number of fiducials = 6
Maximum length for a gate string in ds = 30
Number of LGST strings =  92
Number of LSGST strings =  [92, 488, 884, 1280]


### Test using dimension-4 fake data

In [7]:
#Run LGST to get an initial estimate for the gates in gs_target based on the data in ds
# NOTE: with nSamples less than 1M (100K, 10K, 1K) this routine will choose a higher-than-4 dimensional gateset
ds = dsFake4
gs_lgst4 = pygsti.do_lgst(ds, specs, targetGateset=gs_target, svdTruncateTo=4, verbosity=3)
gs_lgst6 = pygsti.do_lgst(ds, specs, targetGateset=gs_target, svdTruncateTo=6, verbosity=3)

#Print chi^2 of 4-dim and 6-dim estimates
chiSq4 = pygsti.chi2(ds, gs_lgst4, lgstList, minProbClipForWeighting=1e-4)
chiSq6 = pygsti.chi2(ds, gs_lgst6, lgstList, minProbClipForWeighting=1e-4)
print "LGST dim=4 chiSq = ",chiSq4
print "LGST dim=6 chiSq = ",chiSq6

# Least squares GST with model selection
gs_lsgst = pygsti.do_iterative_mc2gst_with_model_selection(ds, gs_lgst4, 1, lsgstLists, verbosity=2,
                                                           minProbClipForWeighting=1e-3, probClipInterval=(-1e5,1e5))

LGST: Singular values of I_tilde (truncating to first 4 of 6) = 
[  3.00484791e+00   8.25822588e-01   6.70903966e-01   6.65330643e-01
   1.32123551e-03   7.62101431e-04]

--- LGST ---
LGST: Singular values of I_tilde (truncating to first 6 of 6) = 
[  3.00484791e+00   8.25822588e-01   6.70903966e-01   6.65330643e-01
   1.32123551e-03   7.62101431e-04]
LGST: Padding target B with sqrt of low singular values of I_tilde: 
[ 0.00132124  0.0007621 ]

--- LGST ---
LGST dim=4 chiSq =  584.010103572
LGST dim=6 chiSq =  218.874929215

--- Iterative LSGST: Beginning iter 1 of 4 : 92 gate strings ---
--- Least Squares GST with model selection (starting dim = 4) ---
--- Least Squares GST ---
  Sum of Chi^2 = 58.5712 (92 data params - 40 model params = expected mean of 52; p-value = 0.247042)
Dim 4: chi^2 = 58.5712, nGateStrings=92, nParams=56 (so expected mean = 36)
--- Least Squares GST ---
  Sum of Chi^2 = 5.51511e+06 (92 data params - 24 model params = expected mean of 68; p-value = 0)
Rejected

In [8]:
print gs_lsgst

rhoVec[0] =    0.7071   0.0245  -0.0259   0.7537


EVec[0] =    0.6838  -0.0010   0.0062  -0.6413


Gi = 
   1.0000        0        0        0
   0.0033   0.9001  -0.0001   0.0003
  -0.0037        0   0.8998   0.0002
  -0.0038  -0.0001   0.0002   0.9000


Gx = 
   1.0000        0        0        0
   0.0030   0.8998   0.0120  -0.0166
  -0.0019   0.0023  -0.0104   0.9883
  -0.0674  -0.0003  -0.8197   0.0103


Gy = 
   1.0000        0        0        0
  -0.0047   0.0004  -0.0038  -0.9997
  -0.0038  -0.0004   0.9000  -0.0020
  -0.0622   0.8102   0.0207  -0.0006





### Test using dimension-5 fake data

In [9]:
#Run LGST to get an initial estimate for the gates in gs_target based on the data in ds
ds = dsFake5
gs_lgst4 = pygsti.do_lgst(ds, specs, targetGateset=gs_target, svdTruncateTo=4, verbosity=3)
gs_lgst6 = pygsti.do_lgst(ds, specs, targetGateset=gs_target, svdTruncateTo=6, verbosity=3)

#Print chi^2 of 4-dim and 6-dim estimates
chiSq4 = pygsti.chi2(ds, gs_lgst4, lgstList, minProbClipForWeighting=1e-2)
chiSq6 = pygsti.chi2(ds, gs_lgst6, lgstList, minProbClipForWeighting=1e-2)
print "LGST dim=4 chiSq = ",chiSq4
print "LGST dim=6 chiSq = ",chiSq6

# Least squares GST with model selection
gs_lsgst = pygsti.do_iterative_mc2gst_with_model_selection(ds, gs_lgst4, 1, lsgstLists, verbosity=2, minProbClipForWeighting=1e-3, probClipInterval=(-1e5,1e5), useFreqWeightedChiSq=False, regularizeFactor=1.0, check=False, check_jacobian=False)

LGST: Singular values of I_tilde (truncating to first 4 of 6) = 
[  2.36368304e+00   6.59319496e-01   4.68883491e-01   4.54819490e-01
   3.15418560e-03   8.91359166e-04]

--- LGST ---
LGST: Singular values of I_tilde (truncating to first 6 of 6) = 
[  2.36368304e+00   6.59319496e-01   4.68883491e-01   4.54819490e-01
   3.15418560e-03   8.91359166e-04]
LGST: Padding target B with sqrt of low singular values of I_tilde: 
[ 0.00315419  0.00089136]

--- LGST ---
LGST dim=4 chiSq =  1316593.37275
LGST dim=6 chiSq =  580943.33613

--- Iterative LSGST: Beginning iter 1 of 4 : 92 gate strings ---
--- Least Squares GST with model selection (starting dim = 4) ---
--- Least Squares GST ---
  Sum of Chi^2 = 143358 (92 data params - 40 model params = expected mean of 52; p-value = 0)
Dim 4: chi^2 = 143358, nGateStrings=92, nParams=56 (so expected mean = 36)
--- Least Squares GST ---
  Sum of Chi^2 = 3.0845e+06 (92 data params - 24 model params = expected mean of 68; p-value = 0)
Rejected dim 3: chi

In [10]:
print gs_lsgst

rhoVec[0] =    0.7070   0.0050  -0.0639   0.7780   0.0234


EVec[0] =    0.5716  -0.0291   0.0344  -0.5175   0.0379


Gi = 
   1.0000        0        0        0        0
  -0.0021   0.8993   0.0010   0.0006  -0.0087
   0.0017   0.0010   0.8984   0.0002   0.0092
  -0.0252  -0.0031   0.0042   0.9006  -0.0321
  -0.0007   0.0089  -0.0123  -0.0017   1.0004


Gx = 
   1.0000        0        0        0        0
   0.0225   0.8381  -0.0553   0.0334   0.0170
   0.1321   0.1337  -0.0508   0.9314   0.2930
  -0.1495  -0.0125  -0.7087   0.0713  -0.1649
  -0.2761  -0.0055  -0.0912  -0.0781   0.7522


Gy = 
   1.0000        0        0        0        0
  -0.1373  -0.0720   0.1428  -0.9426  -0.2899
  -0.0175  -0.1133   0.8380  -0.0076  -0.0112
  -0.1399   0.7026   0.0437   0.1038  -0.1646
  -0.2799   0.0572   0.0165  -0.1096   0.7421



